# Open street map example
The zombie outbreak model showcases an ABM running on a map, using `OpenStreetMapSpace`.

In [1]:
using Agents
using Random
using CairoMakie
using OSMMakie
CairoMakie.activate!(px_per_unit = 1.0)

The helper function is adapted from `Agents.abmvideo` and correctly displays animations in Jupyter notebooks

In [2]:
function abmvio(model;
    dt = 1, framerate = 30, frames = 300, title = "", showstep = true,
    figure = (size = (600, 600),), axis = NamedTuple(),
    recordkwargs = (compression = 23, format ="mp4"), kwargs...
)
    # title and steps
    abmtime_obs = Observable(abmtime(model))
    if title ≠ "" && showstep
        t = lift(x -> title*", time = "*string(x), abmtime_obs)
    elseif showstep
        t = lift(x -> "time = "*string(x), abmtime_obs)
    else
        t = title
    end

    axis = (title = t, titlealign = :left, axis...)
    # First frame
    fig, ax, abmobs = abmplot(model; add_controls = false, warn_deprecation = false, figure, axis, kwargs...)
    resize_to_layout!(fig)
    # Animation
    Makie.Record(fig; framerate, recordkwargs...) do io
        for j in 1:frames-1
            recordframe!(io)
            Agents.step!(abmobs, dt)
            abmtime_obs[] = abmtime(model)
        end
        recordframe!(io)
    end
end

abmvio (generic function with 1 method)

Agents for zombies and healthy humans

In [3]:
@agent struct Zombie(OSMAgent)
    infected::Bool
    speed::Float64
end

initialise model

In [4]:
function initialise_zombies(; seed = 1234)
    map_path = OSM.test_map()
    properties = Dict(:dt => 1 / 60)

    model = StandardABM(
        Zombie,
        OpenStreetMapSpace(map_path);
        agent_step! = zombie_step!,
        properties = properties,
        rng = Random.MersenneTwister(seed)
    )

    for id in 1:100
        start = random_position(model) ## At an intersection
        speed = rand(abmrng(model)) * 5.0 + 2.0 ## Random speed from 2-7kmph
        human = add_agent!(start, Zombie, model, false, speed)
        OSM.plan_random_route!(human, model; limit = 50) ## try 50 times to find a random route
    end

    # We'll add patient zero at a specific (longitude, latitude)
    start = OSM.nearest_road((9.9351811, 51.5328328), model)
    finish = OSM.nearest_node((9.945125635913511, 51.530876112711745), model)

    speed = rand(abmrng(model)) * 5.0 + 2.0 ## Random speed from 2-7kmph
    zombie = add_agent!(start, model, true, speed)
    plan_route!(zombie, finish, model)
    return model
end

initialise_zombies (generic function with 1 method)

Stepping function

In [5]:
function zombie_step!(agent, model)
    # Each agent will progress along their route
    # Keep track of distance left to move this step, in case the agent reaches its
    # destination early
    distance_left = move_along_route!(agent, model, agent.speed * model.dt)

    if is_stationary(agent, model) && rand(abmrng(model)) < 0.1
        # When stationary, give the agent a 10% chance of going somewhere else
        OSM.plan_random_route!(agent, model; limit = 50)
        # Start on new route, moving the remaining distance
        move_along_route!(agent, model, distance_left)
    end

    # Agents will be infected if they get too close (within 10m) to a zombie.
    if agent.infected
        map(i -> model[i].infected = true, nearby_ids(agent, model, 0.01))
    end
    return
end

zombie_step! (generic function with 1 method)

## Animation

In [6]:
zombie_color(agent) = agent.infected ? :green : :black
zombie_size(agent) = agent.infected ? 10 : 8
zombies = initialise_zombies()

vio = abmvio(zombies;
    title = "Zombie outbreak", framerate = 15, frames = 200,
    agent_color = zombie_color, agent_size = zombie_size
)

save("zombie.mp4", vio)
vio |> display

[ Info: Created OSMGraph object with kwargs: `network_type=drive`, `weight_type=distance`, `graph_type=static`, `precompute_dijkstra_states=false`, `largest_connected_component=true`


Makie.VideoStream(Base.PipeEndpoint(RawFD(-1) closed, 0 bytes waiting), Process(setenv(`/home/runner/.julia/artifacts/fdb14f7b1bf6766687af4e3951c4d982cee66086/bin/ffmpeg -y -loglevel quiet -threads 4 -framerate 15 -pixel_format rgb24 -f rawvideo -s:v 600x600 -r 15 -i pipe:0 -vf vflip -profile:v high422 -crf 23 -preset slow -c:v libx264 -pix_fmt yuv420p -an '/tmp/jl_sUXGJV/##video#233.mp4'`,["JULIA_CI=true", "PATH=/home/runner/.julia/artifacts/2ab21f29b30c228bd0e5215585f822730cad5a72/bin:/home/runner/.julia/artifacts/0ccc8805e5047cf9fbd848c4f7d4c15715aad7c9/bin:/home/runner/.julia/artifacts/96bc7b9ddb319d1a051535c85184aa2bf42dbd8b/bin:/home/runner/.julia/artifacts/bd752d7807f5f10e2dce3d2b2b683589fa03d31a/bin:/home/runner/.julia/artifacts/c8a20a2030f10b70947d8d2a6bff7f8b5f343fe9/bin:/home/runner/.julia/artifacts/1cf7375e8ec1bbe1219934488737c12237ba2012/bin:/home/runner/.julia/artifacts/aa47becfd7dbea936fcdbe2abc2c5637739026df/bin:/home/runner/.julia/artifacts/00023f2f62a04af7531278ce1a689ff93800ffa1/bin:/home/runner/.julia/artifacts/c951fb23b5652def1dea483af7095a38f3b3cefd/bin:/home/runner/.julia/artifacts/fdb14f7b1bf6766687af4e3951c4d982cee66086/bin:/opt/hostedtoolcache/julia/1.11.2/x64/bin:/opt/hostedtoolcache/Python/3.12.8/x64/bin:/opt/hostedtoolcache/Python/3.12.8/x64:/snap/bin:/home/runner/.local/bin:/opt/pipx_bin:/home/runner/.cargo/bin:/home/runner/.config/composer/vendor/bin:/usr/local/.ghcup/bin:/home/runner/.dotnet/tools:/usr/local/sbin:/usr/local/bin:/usr/sbin:/usr/bin:/sbin:/bin:/usr/games:/usr/local/games:/snap/bin", "DOTNET_SKIP_FIRST_TIME_EXPERIENCE=1", "GITHUB_RUN_NUMBER=464", "GITHUB_REF_NAME=main", "RUNNER_ARCH=X64", "STATS_PIP=false", "PERFLOG_LOCATION_SETTING=RUNNER_PERFLOG", "LD_LIBRARY_PATH=/home/runner/.julia/artifacts/f839432e3d2904a5c847b217ef0c0f489377ecc5/lib:/opt/hostedtoolcache/julia/1.11.2/x64/bin/../lib/julia:/home/runner/.julia/artifacts/a0f4f1441f9fabbc6b0c3a1bf38bfa415fce0bab/lib:/home/runner/.julia/artifacts/2ab21f29b30c228bd0e5215585f822730cad5a72/lib:/home/runner/.julia/artifacts/2def0eca464bd6d89ccac85338474402359d4930/lib:/home/runner/.julia/artifacts/d00220164876dea2cb19993200662745eed5e2db/lib:/home/runner/.julia/artifacts/0ccc8805e5047cf9fbd848c4f7d4c15715aad7c9/lib:/home/runner/.julia/artifacts/dc526f26fb179a3f68eb13fcbe5d2d2a5aa7eeac/lib:/home/runner/.julia/artifacts/78b3ee512bee8cbd79df0ebeb2aaea0b9057aeb0/lib:/home/runner/.julia/artifacts/43964d8fde379b95f9b4bdc214b688bc394cd4ac/lib:/home/runner/.julia/artifacts/b3ddd583e7aec92a77cf5961fad01fd7063c1d40/lib:/home/runner/.julia/artifacts/7099954ffb0b6e1641832a06a08e479498ce479f/lib:/home/runner/.julia/artifacts/12a47720c355272eccbb34476fe4404f1a0a3036/lib:/home/runner/.julia/artifacts/96bc7b9ddb319d1a051535c85184aa2bf42dbd8b/lib:/home/runner/.julia/artifacts/bd752d7807f5f10e2dce3d2b2b683589fa03d31a/lib:/home/runner/.julia/artifacts/7328e6b9e83b8ce9ad81ab14feff0d72eca94bb7/lib:/home/runner/.julia/artifacts/7ac675eff20f2e2781e828815d4fe9c06df0f0e3/lib:/home/runner/.julia/artifacts/2bb2b0081086bcb24e6bd287b7416b6b61d856a3/lib:/home/runner/.julia/artifacts/d632a0145c0b967e10f0612438e65bf33ce26882/lib:/home/runner/.julia/artifacts/2b9ac56bc0585f3b03cd92f988f0d07c6ab12822/lib:/home/runner/.julia/artifacts/8223b86c51229362d4689de6a5127d0b80ea77bd/lib:/home/runner/.julia/artifacts/6f98018cad6a09e91f90658f188c6be47e48a0c7/lib:/home/runner/.julia/artifacts/d4f3ff9736df0dda120f8dc1d27174b0d5696fb1/lib:/home/runner/.julia/artifacts/eb13375496c29fe52101a0e6710c54ff87aa0e20/lib:/home/runner/.julia/artifacts/3ded11a619b50414af902abd0a7a5bb6426b5b92/lib:/home/runner/.julia/artifacts/bd1f25e7053ebc00ee7d82f3c5ec4cf1e9a51e17/lib:/home/runner/.julia/artifacts/cf5d5f8a6109be3f9c460a39768f57a3e53ff11d/lib:/home/runner/.julia/artifacts/c8a20a2030f10b70947d8d2a6bff7f8b5f343fe9/lib:/home/runner/.julia/artifacts/0631e2a6a31b5692eec7a575836451b16b734ec0/lib:/home/runner/.julia/artifacts/4abd0521d210cb9e48ea5e711873ba34dc05fc70/lib:/home/runner/.julia/artifacts/

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*